**If you like my notebook, please upvote my work!**

**If you use parts of this notebook in your scripts/notebooks, giving some kind of credit for instance link back to this notebook would be very much appreciated. Thanks in advance! :)**

P.S:

1. The script in line 5 shows error when run on kaggle(And have therefore been commented) but will run perfectly fine after downloading and running the script on local machine.

2. Please make sure that you have plotly installed on your local machine.

Lastly if anyone knows how to fix the above problem please let me know. Thankyou! :) Hope you like my work!

In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load in 

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the "../input/" directory.
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# Any results you write to the current directory are saved as output.

# Importing important modules.

In [2]:
import xgboost as xg
import seaborn as sb
import plotly.express as px
from matplotlib import pyplot as plt
from sklearn.decomposition import PCA
from sklearn.metrics import make_scorer
from sklearn.metrics import roc_auc_score
from sklearn.naive_bayes import BernoulliNB
from sklearn.model_selection import GridSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split
from sklearn.gaussian_process import GaussianProcessClassifier

# Loading the training dataset.

In [3]:
df_train = pd.read_csv('./train.csv')

In [4]:
df_train.describe()

id      target           0           1           2           3  \
count  250.000000  250.000000  250.000000  250.000000  250.000000  250.000000   
mean   124.500000    0.268000   -0.098064    0.001208    0.090680   -0.122248   
std     72.312977    0.443806    0.996063    0.955117    0.968065    0.933001   
min      0.000000    0.000000   -3.181000   -3.041000   -2.967000   -2.898000   
25%     62.250000    0.000000   -0.756250   -0.624750   -0.515750   -0.695500   
50%    124.500000    0.000000   -0.064500   -0.008000    0.067500   -0.090000   
75%    186.750000    1.000000    0.647750    0.493250    0.716000    0.436250   
max    249.000000    1.000000    2.347000    3.138000    2.609000    2.590000   

                4           5           6           7  ...         290  \
count  250.000000  250.000000  250.000000  250.000000  ...  250.000000   
mean     0.011500   -0.116624    0.006932    0.100988  ...    0.013052   
std      0.945662    1.081705    1.014091    1.028042  ...    1.027845   
min     -2.837000   -3.831000   -2.873000   -2.489000  ...   -2.824000   
25%     -0.678000   -0.758500   -0.646250   -0.589000  ...   -0.764000   
50%      0.028000   -0.073500   -0.076500    0.104500  ...    0.017500   
75%      0.625250    0.554250    0.676500    0.717000  ...    0.690500   
max      2.413000    2.687000    2.793000    3.766000  ...    2.773000   

              291         292         293         294         295         296  \
count  250.000000  250.000000  250.000000  250.000000  250.000000  250.000000   
mean     0.007500    0.000452    0.060276   -0.090308   -0.040728   -0.002132   
std      1.048169    1.026398    1.048744    1.008657    1.051273    1.065524   
min     -2.971000   -3.592000   -3.071000   -2.621000   -3.013000   -3.275000   
25%     -0.729250   -0.699750   -0.589000   -0.701000   -0.696750   -0.555750   
50%      0.053000    0.029500    0.042500   -0.102000   -0.057000    0.094500   
75%      0.665000    0.670750    0.713250    0.532250    0.727000    0.590000   
max      2.701000    3.193000    4.280000    2.716000    3.074000    2.626000   

              297         298         299  
count  250.000000  250.000000  250.000000  
mean    -0.012540   -0.039904    0.073236  
std      0.958744    0.948251    0.924989  
min     -2.665000   -3.006000   -2.471000  
25%     -0.677500   -0.719750   -0.559000  
50%     -0.025500   -0.027500    0.160500  
75%      0.671000    0.717000    0.711000  
max      2.388000    2.730000    3.401000  

[8 rows x 302 columns]

## Plotting the covarience matrix.

In [5]:
corr = df_train.drop('id',axis =1).corr()
column = df_train.drop('id',axis = 1).columns

fig = px.imshow(img = corr,#x = column , y = column,
                color_continuous_scale = [[0,'white'],[0.42,'yellow'],
                                          [0.58,'red'],[1.0,'black']],
                labels = {'x':"Column", 'y': 'Row', 'color':'Correlation'},
                height = 1100,width = 1100,color_continuous_midpoint = 0,
                title = 'Correlation matrix for all fields.')
fig.show()

**The column 0 corrosponds to the target variable**

# Data processing.

## Separating training and testing data.

In [6]:
df_train_x = df_train.drop(['id','target'],axis=1)
df_train_y = df_train[['target']]
df_train_x.describe()

0           1           2           3           4           5  \
count  250.000000  250.000000  250.000000  250.000000  250.000000  250.000000   
mean    -0.098064    0.001208    0.090680   -0.122248    0.011500   -0.116624   
std      0.996063    0.955117    0.968065    0.933001    0.945662    1.081705   
min     -3.181000   -3.041000   -2.967000   -2.898000   -2.837000   -3.831000   
25%     -0.756250   -0.624750   -0.515750   -0.695500   -0.678000   -0.758500   
50%     -0.064500   -0.008000    0.067500   -0.090000    0.028000   -0.073500   
75%      0.647750    0.493250    0.716000    0.436250    0.625250    0.554250   
max      2.347000    3.138000    2.609000    2.590000    2.413000    2.687000   

                6           7           8           9  ...         290  \
count  250.000000  250.000000  250.000000  250.000000  ...  250.000000   
mean     0.006932    0.100988   -0.044960    0.007768  ...    0.013052   
std      1.014091    1.028042    0.893491    1.010694  ...    1.027845   
min     -2.873000   -2.489000   -2.346000   -2.753000  ...   -2.824000   
25%     -0.646250   -0.589000   -0.563000   -0.715500  ...   -0.764000   
50%     -0.076500    0.104500   -0.018500    0.003000  ...    0.017500   
75%      0.676500    0.717000    0.544750    0.709500  ...    0.690500   
max      2.793000    3.766000    1.990000    2.602000  ...    2.773000   

              291         292         293         294         295         296  \
count  250.000000  250.000000  250.000000  250.000000  250.000000  250.000000   
mean     0.007500    0.000452    0.060276   -0.090308   -0.040728   -0.002132   
std      1.048169    1.026398    1.048744    1.008657    1.051273    1.065524   
min     -2.971000   -3.592000   -3.071000   -2.621000   -3.013000   -3.275000   
25%     -0.729250   -0.699750   -0.589000   -0.701000   -0.696750   -0.555750   
50%      0.053000    0.029500    0.042500   -0.102000   -0.057000    0.094500   
75%      0.665000    0.670750    0.713250    0.532250    0.727000    0.590000   
max      2.701000    3.193000    4.280000    2.716000    3.074000    2.626000   

              297         298         299  
count  250.000000  250.000000  250.000000  
mean    -0.012540   -0.039904    0.073236  
std      0.958744    0.948251    0.924989  
min     -2.665000   -3.006000   -2.471000  
25%     -0.677500   -0.719750   -0.559000  
50%     -0.025500   -0.027500    0.160500  
75%      0.671000    0.717000    0.711000  
max      2.388000    2.730000    3.401000  

[8 rows x 300 columns]

In [7]:
df_train_y.describe()

target
count  250.000000
mean     0.268000
std      0.443806
min      0.000000
25%      0.000000
50%      0.000000
75%      1.000000
max      1.000000

# Testing various models to check which one works best.

In [8]:
models = ['Gaussian Classifier','Bernaulli Classifier','Random Forest Classifier',
          'XGBoost Classifier']

### Defining a custom scorer function.

In [9]:
def custom_scorer(y_true,y_pred):
    return roc_auc_score(y_true,y_pred)
scorer = make_scorer(custom_scorer,greater_is_better = True)

## Defining the parameters for grid search

In [10]:
gauss = GaussianProcessClassifier()
gauss_dic = {'warm_start':[True,False],'multi_class':["one_vs_rest","one_vs_one"],
             'n_restarts_optimizer':[0,1,2],'max_iter_predict': [20,50,100]}

bernoulli = BernoulliNB()
bernoulli_dic = {'alpha' : [0,1,2,4,8]}

forest = RandomForestClassifier()
forest_dic = {'n_estimators': [10,20,30,40],'criterion':['geni','entropy'],
              'max_depth':[2,4,6,8,10]}

xgb = xg.XGBClassifier()
xgb_dic = {'max_depth':[2,4,6,8,10,12],"eta": [0.01,0.03,0.05],'gamma' : [0,0.00001,0.0001,0.001]}

## Calculating the score for different models

In [11]:
best_params = []
best_score = []
gauss_clf = GridSearchCV(gauss,gauss_dic,cv=9,scoring = scorer,n_jobs =-1)
gauss_clf.fit(df_train_x,df_train_y.to_numpy().ravel())
best_params.append(gauss_clf.best_params_)
best_score.append(gauss_clf.best_score_)

bernoulli_clf = GridSearchCV(bernoulli,bernoulli_dic,cv=9,scoring = scorer,n_jobs =-1)
bernoulli_clf.fit(df_train_x,df_train_y.to_numpy().ravel())
best_params.append(bernoulli_clf.best_params_)
best_score.append(bernoulli_clf.best_score_)

forest_clf = GridSearchCV(forest,forest_dic,cv=9,scoring = scorer,n_jobs =-1)
forest_clf.fit(df_train_x,df_train_y.to_numpy().ravel())
best_params.append(forest_clf.best_params_)
best_score.append(forest_clf.best_score_)

xgb_clf = GridSearchCV(xgb,xgb_dic,cv=9,scoring = scorer,n_jobs =-1)
xgb_clf.fit(df_train_x,df_train_y.to_numpy().ravel())
best_params.append(xgb_clf.best_params_)
best_score.append(xgb_clf.best_score_)

/opt/conda/lib/python3.6/site-packages/sklearn/naive_bayes.py:507: UserWarning:

alpha too small will result in numeric errors, setting alpha = 1.0e-10



In [12]:
for i in range (4):
    print ('The best  parameters for the model ' + models[i] + 'are : '+ str(best_params[i]) )
    print ('The score obtained using the model ' + models[i] + 'is : '+ str(best_score[i]) )

The best  parameters for the model Gaussian Classifierare : {'max_iter_predict': 20, 'multi_class': 'one_vs_rest', 'n_restarts_optimizer': 0, 'warm_start': True}
The score obtained using the model Gaussian Classifieris : 0.5078042328042327
The best  parameters for the model Bernaulli Classifierare : {'alpha': 0}
The score obtained using the model Bernaulli Classifieris : 0.5322089947089946
The best  parameters for the model Random Forest Classifierare : {'criterion': 'entropy', 'max_depth': 6, 'n_estimators': 10}
The score obtained using the model Random Forest Classifieris : 0.5218253968253969
The best  parameters for the model XGBoost Classifierare : {'eta': 0.03, 'gamma': 0, 'max_depth': 8}
The score obtained using the model XGBoost Classifieris : 0.5610449735449736


Since the score obtained using the XGBoost model is the highest, we use the XGBoost classifier as our final model.

# Loading the testing dataset.

In [13]:
df_test = pd.read_csv('/kaggle/input/dont-overfit-ii/test.csv')
df_test.describe()

id             0             1             2             3  \
count  19750.000000  19750.000000  19750.000000  19750.000000  19750.000000   
mean   10124.500000      0.010933     -0.005470      0.003176     -0.000584   
std     5701.478244      0.997062      1.002163      1.001684      0.992821   
min      250.000000     -4.109000     -4.613000     -3.749000     -3.685000   
25%     5187.250000     -0.667000     -0.673000     -0.669000     -0.673750   
50%    10124.500000      0.017000     -0.006000     -0.000000     -0.004500   
75%    15061.750000      0.689000      0.674000      0.675000      0.660000   
max    19999.000000      3.775000      3.725000      3.922000      3.969000   

                  4             5             6             7             8  \
count  19750.000000  19750.000000  19750.000000  19750.000000  19750.000000   
mean      -0.011377      0.001225      0.008716     -0.003512     -0.005035   
std        0.997261      1.002442      1.003023      1.004868      0.998808   
min       -3.711000     -3.911000     -4.863000     -3.879000     -4.051000   
25%       -0.678750     -0.683750     -0.670000     -0.674000     -0.691000   
50%       -0.013000      0.000000      0.014000     -0.003000     -0.010000   
75%        0.661000      0.676000      0.694750      0.670000      0.667000   
max        3.806000      3.744000      3.733000      4.199000      3.475000   

       ...           290           291           292           293  \
count  ...  19750.000000  19750.000000  19750.000000  19750.000000   
mean   ...      0.002145      0.004692      0.004862     -0.002706   
std    ...      1.000769      0.999980      0.998581      0.993671   
min    ...     -4.444000     -3.879000     -3.919000     -3.632000   
25%    ...     -0.676000     -0.668000     -0.680000     -0.680000   
50%    ...      0.004000      0.006000      0.005000     -0.006000   
75%    ...      0.681000      0.677000      0.684750      0.665000   
max    ...      4.072000      3.911000      3.580000      3.823000   

                294           295           296           297           298  \
count  19750.000000  19750.000000  19750.000000  19750.000000  19750.000000   
mean       0.004469     -0.003974     -0.003001     -0.005502      0.011342   
std        0.996648      1.008269      1.002226      0.996583      1.003967   
min       -3.783000     -3.950000     -4.052000     -3.695000     -3.760000   
25%       -0.670000     -0.686000     -0.681000     -0.683000     -0.675750   
50%        0.003000     -0.001000      0.004000     -0.016000      0.009500   
75%        0.682750      0.675750      0.668000      0.666750      0.692000   
max        3.643000      5.042000      3.798000      3.779000      4.190000   

                299  
count  19750.000000  
mean       0.004954  
std        0.998843  
min       -3.740000  
25%       -0.667000  
50%        0.009500  
75%        0.676000  
max        3.796000  

[8 rows x 301 columns]

In [14]:
output= df_test[['id']]
df_test = df_test.drop('id',axis = 1)

## Predicting result using the model over the test set.

In [15]:
output['xgb'] = xgb_clf.predict(df_test)
output['target'] = output['xgb']

# Exporting the result to csv.

In [16]:
output[['id','target']].to_csv('Submission.csv',index = False)